# Выбор локации для скважины

Мы работаем в добывающей компании «ГлавРосГосНефть». Нужно решить, где бурить новую скважину.

Нам предоставлены пробы нефти в трёх регионах: в каждом 10 000 месторождений, где измерили качество нефти и объём её запасов. Построим модель машинного обучения, которая поможет определить регион, где добыча принесёт наибольшую прибыль. Проанализируем возможную прибыль и риски техникой *Bootstrap.*

Шаги для выбора локации:

- В избранном регионе ищут месторождения, для каждого определяют значения признаков;
- Строят модель и оценивают объём запасов;
- Выбирают месторождения с самым высокими оценками значений. Количество месторождений зависит от бюджета компании и стоимости разработки одной скважины;
- Прибыль равна суммарной прибыли отобранных месторождений.

<h1>Содержание<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Загрузка-и-подготовка-данных" data-toc-modified-id="Загрузка-и-подготовка-данных-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Загрузка и подготовка данных</a></span></li><li><span><a href="#Обучение-и-проверка-модели" data-toc-modified-id="Обучение-и-проверка-модели-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Обучение и проверка модели</a></span></li><li><span><a href="#Подготовка-к-расчёту-прибыли" data-toc-modified-id="Подготовка-к-расчёту-прибыли-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Подготовка к расчёту прибыли</a></span></li><li><span><a href="#Расчёт-прибыли-и-рисков" data-toc-modified-id="Расчёт-прибыли-и-рисков-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Расчёт прибыли и рисков</a></span></li><li><span><a href="#Итоговый-вывод" data-toc-modified-id="Итоговый-вывод-5"><span class="toc-item-num">5&nbsp;&nbsp;</span>Итоговый вывод</a></span></li><li><span><a href="#Чек-лист-готовности-проекта" data-toc-modified-id="Чек-лист-готовности-проекта-6"><span class="toc-item-num">6&nbsp;&nbsp;</span>Чек-лист готовности проекта</a></span></li></ul></div>

**Описание данных**

В нашем распоряжении три датасета с пробами нефти в трёх разных регионах. В данных имеется:
- id — уникальный идентификатор скважины;
- f0, f1, f2 — три признака точек (к сожалению подробности о признаках нам не передали, но намекнули, что признаки значимы);
- product — объём запасов в скважине (тыс. баррелей).

In [1]:
import sklearn # Проверка версии sklearn. Обновляем при необходимости
if sklearn.__version__ == '0.24.1':
    !pip install scikit-learn -U # После установки надо перезапустить ядро
sklearn.__version__ 

'1.4.2'

In [2]:
import pandas as pd 
import matplotlib.pyplot as plt
import seaborn as sns
from IPython.display import display
import numpy as np
try:
    from ydata_profiling import ProfileReport
except:
    !pip install -U ydata-profiling
    from ydata_profiling import ProfileReport

from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split

from sklearn.linear_model import LinearRegression
from sklearn.metrics import root_mean_squared_error

In [3]:
sns.set(style='darkgrid', palette='deep') # Устанавливаем стиль для графиков
RANDOM_STATE = 42 # Константа определения случайных значений 

## Загрузка и подготовка данных

Для начала познакомимся с нашими данными.

In [4]:
try:
    ds_0 = pd.read_csv('/datasets/geo_data_0.csv', index_col='id')
except:
    ds_0 = pd.read_csv('datasets/geo_data_0.csv', index_col='id')
ProfileReport(ds_0)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Ни пропусков, ни дубликатов. Типы данных в норме, распределение признака f2 выглядит как идеальное нормальное, в остальных случаях варьируется от признака к признаку, но аномальных значений нет. f1 и f0 имеют умеренную обратную корреляцию, но до мультиколлениарности ещё далеко. f2 умеренно коррелирует с целевым признаком. Линейные зависимости важны для линейных моделей, так-что для нас это хорошо.

In [5]:
try:
    ds_1 = pd.read_csv('/datasets/geo_data_1.csv', index_col='id')
except:
    ds_1 = pd.read_csv('datasets/geo_data_1.csv', index_col='id')
ProfileReport(ds_1)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

f2 и product крайне смахивают на категориальные переменные, но в них всё-же занесены непрерывные числа, крайне близкие к целым значениям. Это чем-то похоже на округление, произошедшее с ошибкой, но мы уже ничего не сможем с ними сделать, придётся использовать эти данные. Почти полная линейная зависимость f2 и целевого признака. Это могло-бы быть проблемой, но не для линейной модели. Крайне много нулей в значениях продукта, около 8%. На это может существовать своя причина, как связанная с нефтяной отраслью, например пустые или крайне малоёмкие скважины, так итехническая ошибка, например при всё том-же округлении. Пока мы не можем сказать наверняка - лучше не будем трогать данные, они могут быть нам полезны.

In [6]:
try:
    ds_2 = pd.read_csv('/datasets/geo_data_2.csv', index_col='id')
except:
    ds_2 = pd.read_csv('datasets/geo_data_2.csv', index_col='id')
ProfileReport(ds_2)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Все распределения похожи на нормальные. Признак f2 умеренно коррелирует с целевым признаком, все остальные признаки показывают нулевую корреляцию.

Все имеющиеся у нас данные, за исключением айди - численные. Тут не обойтись без скейлера.

In [7]:
data_preprocessor = ColumnTransformer([
    ('num', MinMaxScaler(), ['f0', 'f1', 'f2'])
])

## Обучение и проверка модели

Нам необходимо обучить 3 модели, по одной на каждый регион. Для обучения нам подойдёт только линейная регрессия, остальные недостаточно предсказуемы. 

In [8]:
lr_0 = Pipeline([ 
    ('preprocessor', data_preprocessor),
    ('model', LinearRegression()) 
]) 
lr_1 = Pipeline([ 
    ('preprocessor', data_preprocessor),
    ('model', LinearRegression()) 
]) 
lr_2 = Pipeline([ 
    ('preprocessor', data_preprocessor),
    ('model', LinearRegression()) 
]) 

Теперь необходимо разделить данные. Нам нужны обучающие и валидационные выборки в соотношении 75:25 для каждого датасета.

In [9]:
X_train_0, X_valid_0, y_train_0, y_valid_0 = train_test_split(ds_0.drop('product', axis=1), ds_0['product'], test_size=0.25, random_state=RANDOM_STATE)
X_train_1, X_valid_1, y_train_1, y_valid_1 = train_test_split(ds_1.drop('product', axis=1), ds_1['product'], test_size=0.25, random_state=RANDOM_STATE)
X_train_2, X_valid_2, y_train_2, y_valid_2 = train_test_split(ds_2.drop('product', axis=1), ds_2['product'], test_size=0.25, random_state=RANDOM_STATE)

Обучим модели, и сразу попросим сделать предсказания.

In [10]:
lr_0.fit(X_train_0, y_train_0)
y_pred_0 = lr_0.predict(X_valid_0)

lr_1.fit(X_train_1, y_train_1)
y_pred_1 = lr_1.predict(X_valid_1)

lr_2.fit(X_train_2, y_train_2)
y_pred_2 = lr_2.predict(X_valid_2)

Для вывода метрики, за которую мы возьмём RMSE - корень из среднего значения квадратов ошибок, создадим функцию, которая будет принимать истинные и предсказанные значения, а также номер региона, и будет выводить все необходимые нам данные.

In [11]:
def rmse_present(true, pred, region):
    print('Модель линейной регрессии для региона №'+str(region))
    print('RMSE модели:', root_mean_squared_error(true, pred).round(4))
    print('Средний запас предсказанного сырья:', pred.mean().round(4))
    print('')

Сделаем список списков с готовыми данными для расчёта метрик, чтобы не обращаться к функции каждый раз вручную. И запустим цикл, который пройдётся по каждому из трёх наборов данных.

In [12]:
rmse_data = [[y_valid_0, y_pred_0, 0], [y_valid_1, y_pred_1, 1], [y_valid_2, y_pred_2, 2]]

for i, j, k in rmse_data:
    rmse_present(i, j, k)

Модель линейной регрессии для региона №0
RMSE модели: 37.7566
Средний запас предсказанного сырья: 92.3988

Модель линейной регрессии для региона №1
RMSE модели: 0.8903
Средний запас предсказанного сырья: 68.7129

Модель линейной регрессии для региона №2
RMSE модели: 40.1459
Средний запас предсказанного сырья: 94.771



Наилучший результат качества предсказаний показала модель для региона номер 1. Оно и не удивительно, при загрузке данных мы обратили внимание на прямую зависимость целевого признака от f2, линейные модели такое любят. По иронии судьбы именно этот регион показал самый низкий средний запас предсказанного сырья. 

## Подготовка к расчёту прибыли

Для начала сохраним ключевые значения для расчётов в отдельные переменные.

In [13]:
SCOUTING_COUNT = 500 # При разведке региона исследуют данное количество точек
SCOUTING_BEST = 200 # Среди них с помощью МО выбирают данное количество лучших для разработки
BUDGET = 10_000_000_000 # Бюджет на разработку скважин в регионе, рублей
INCOME = 450_000 # Прибыль с одной единицы продукта, рублей
LOSS_RISK = .025 # Порог вероятности убытков. После оценки рисков выбираются только регионы, в которых вероятность убытков меньше порога

Теперь рассчитаем достаточный объём сырья для безубыточной разработки новой скважины. Поделим бюджет на прибыль с одной единицы продукта, а после на планируемое количество скважин для разработки. И получим количество единиц продукта, которое каждая скважина должна содержать, чтобы компания не работала себе в убыток.

In [14]:
PAYBACK = round(BUDGET/INCOME/SCOUTING_BEST, 2)
PAYBACK

111.11

111 тысяч баррелей, столько должна содержать скважина, чтобы окупить свою разработку. Это больше средних предсказанных запасов каждого из регионов. Далеко не каждая скважина нам подойдёт, но именно за этим мы здесь и собрались.

## Расчёт прибыли и рисков 

In [15]:
state = np.random.RandomState(RANDOM_STATE) # Определение случайных значений для бутстрепа

Теперь приступим к самому приятному - будем считать прибыль. Пока только теоретическую. Для этого создадим функцию. 

Она будет принимать на вход спрогнозированные значения, отбирать из них заданное количество лучших(`SCOUTING_BEST`), и рассчитывать прибыль по формуле `общий объём сырья` * `прибыль с единицы` - `бюджет на разработку скважин`. 

Также попросим функцию возвращать прибыль с каждой скважины. Это будет `объём сырья` * `прибыль с единицы` - `минимальное содержание сырья для окупаемости` * `прибыль с единицы`

In [16]:
def profit_check(data):
    data = data.sort_values(by=0, ascending=False)
    data = data['product'].head(SCOUTING_BEST)
    capacity = data.sum()
    return float(capacity*INCOME-BUDGET), list(data*INCOME-PAYBACK*INCOME)

Функция готова, теперь бутстреп. Напомню, бутстреп - это техника, при которой имеющиеся данные разбиваются на случайные подвыборки, с которыми уже и производятся вычисления. Мы можем разбивать данные сколько душе угодно, но за основу возьмём 1000 итераций для каждого региона. Итого мы 1000 раз возьмём случайные записи в количестве `SCOUTING_COUNT` из трёх генеральных совокупностей. Эти записи будут имитировать разведанные в регионе скважины, и в каждой итерации мы будем рассчитывать прибыль, которую мы с них получим. Все результаты прибыли мы занесём в список, и позже получим доверительные интервалы, средние значения и риски отрицательной прибыли. Теория есть, приступим к практике.

In [17]:
def bootstrap_check(ds, region):
    incomes = []
    incomes_all = []
    for i in range(1000):
        profit_mean, profits = profit_check(ds.sample(SCOUTING_COUNT, replace=True, random_state=state))
        incomes.append(profit_mean)
        incomes_all.extend(profits)
    incomes = pd.Series(incomes)
    print('Данные по региону №'+str(region))
    print('Средняя прибыль в регионе:', np.mean(incomes))
    print('95%-й доверительный интервал:', np.quantile(incomes_all, .975), np.quantile(incomes_all, .025))
    print('Риск убытков:', (incomes<0).sum()/len(incomes)*100, '%')
    if (incomes<0).sum()/len(incomes)<LOSS_RISK:
        print('Риск убытков проходит по порогу')
    else:
        print('Риск убытков слишком велик, регион бесперспективен')
    print('')
    return incomes

In [18]:
incomes_0 = bootstrap_check(pd.DataFrame(y_pred_0, index=X_valid_0.index).join(pd.DataFrame(y_valid_0, index=X_valid_0.index)), 0)
incomes_1 = bootstrap_check(pd.DataFrame(y_pred_1, index=X_valid_1.index).join(pd.DataFrame(y_valid_1, index=X_valid_1.index)), 1)
incomes_2 = bootstrap_check(pd.DataFrame(y_pred_2, index=X_valid_2.index).join(pd.DataFrame(y_valid_2, index=X_valid_2.index)), 2)

Данные по региону №0
Средняя прибыль в регионе: 399575478.05422974
95%-й доверительный интервал: 30635710.938632697 -35291642.82332828
Риск убытков: 6.0 %
Риск убытков слишком велик, регион бесперспективен

Данные по региону №1
Средняя прибыль в регионе: 452576594.2909005
95%-й доверительный интервал: 12075933.483407535 -12182001.444978155
Риск убытков: 0.8999999999999999 %
Риск убытков проходит по порогу

Данные по региону №2
Средняя прибыль в регионе: 378705903.65973765
95%-й доверительный интервал: 32420762.229762584 -36530271.81341158
Риск убытков: 7.5 %
Риск убытков слишком велик, регион бесперспективен



Регионы 0 и 2 продемонстрировали слишком высокий риск убытков. 

Регион 1 единственный проходит по порогу риска убытков, а также показывает наибольшее среднее значение прогнозной прибыли, и может считаться самым перспективным для разработки новых скважин. Именно его мы и предложим.

Вспоминая обучение моделей, мы можем подметить, что модель региона 1 показала наилучший результат качества прогнозов, и наихудший результат среднего прогнозного сырья. Возвращаясь к ознакомлению с данными, мы также могли увидеть, что регион 1 имеет скудные средние запасы продукта не только по прогнозам, но и в действительности, что скорее всего связано с обилием нулей в данных. Из чего можем сделать вывод, что выбор правильных скважин среди предложенных как минимум не менее важен, чем общее богатство региона. 

## Итоговый вывод

В рамках загрузки и подготовки данных, мы:
- Проверили данные на пропуски и дубликаты;
- Проследили за распределением значений, убедились в отсутствии аномалий;
- Составили заготовку препроцессинга для пайплайнов моделей.

В рамках обучения моделей и проверки качества, мы:
- Составили пайплайны для трёх моделей;
- Обучили три линейные регрессии в пайплайне, на датасетах разных регионов;
- Рассчитали средние значения предсказанного сырья для каждой модели;
- Вывели метрики RMSE для каждой модели.

В рамках подготовки к расчёту прибыли, мы:
- Сохранили ключевые значения для расчётов в переменные. Это позволит легко модифицировать модель при изменении условий работы;
- Рассчитали минимальный объём содержания сырья в каждой скважине, необходимое для её окупаемости.

В рамках расчёта прибыли и рисков, мы:
- Написали функцию для расчёта прибыли по прогнозированным значениям содержания сырья;
- Провели 1000 итераций по технике бутстреп для каждого региона и расчитали итоговую прибыль для каждой подвыборки;
- По полученным значениям расчитали доверительные интервалы, среднюю прибыль в регионе и риски убытков;
- Сделали выводы по перспективности регионов.

Самым перспективным регионом для разработки скважин, на основе средней прогнозной прибыли, доверительного интервала прогнозных значений и риска убытков, был выбран регион №1.

Рекомендации заказчику: 
- Повысить активность в регионе №1.
- Установить причину возникновения нулевых значений продукта в данных о регионе 1.
- Установить причину возникновения прямой зависимости продукта от признака f2 в данных о регионе 1.
- Установить причину аномального распределения значений продукта и f2 в данных о регионе 1.

Регионы 0 и 2 могут показать результат лучше, если у нас получится повысить качество моделей. Лучшим методом здесь будет добавление линейно зависимых признаков. Учитывая различия в корреляции данных разных регионов, возможно в регионе 1 признак f2 рассчитывается иначе, нежели чем в регионах 0 и 2. Если это не является утечкой целевого признака - перенятие методики расчёта признака для других регионов может повысить качество предсказаний, и мы сможем сделать более точные выводы по прибыльности каждого региона.